In [3]:
import pandas as pd
import numpy as np
import nltk
import nltk.sentiment.util
import matplotlib.pyplot as plt
import pprint
import re
import gensim
import gensim.corpora as corpora
import os
from gensim.utils import simple_preprocess
from nltk.corpus import stopwords

In [4]:
df = pd.read_csv("../../amazon_reviews_us_Grocery_v1_00.tsv", sep='\t', quoting=3)
df = df[["product_id", "star_rating", "review_body"]]
df

product_id  star_rating  \
0        B000SAQCWC            5   
1        B00509LVIQ            5   
2        B00KHXESLC            5   
3        B000F8JIIC            5   
4        B004ZWR9RQ            5   
...             ...          ...   
2402453  B00004TBB0            4   
2402454  B00000K1X9            5   
2402455  B00000K1X9            5   
2402456  B00000K1X9            5   
2402457  B00000K1X9            5   

                                               review_body  
0        As a family allergic to wheat, dairy, eggs, nu...  
1        My favorite nut.  Creamy, crunchy, salty, and ...  
2        This green tea tastes so good! My girlfriend l...  
3        I love Melissa's brand but this is a great sec...  
4                                                     good  
...                                                    ...  
2402453  The Amor Belhom Duo are likely the only musici...  
2402454  Being  a  Breyer  collecter  almost  all  of  ...  
2402455  This model is beautiful.  each model is hand p...  
2402456  As a person who has collected Breyers all my l...  
2402457  This Breyer horse is wonderful. She is beautif...  

[2402458 rows x 3 columns]

In [5]:
data = df.dropna()
data = data.query('star_rating == 1', engine='python').sample(10000)

In [6]:
#data['review_body'] = data['review_body'].map(lambda x: re.sub('[,\.!?]', '', x))
#data['review_body'] = data['review_body'].map(lambda x: x.lower())
data = data["review_body"]
data

2342134    The centers of these products were to be fille...
1515968    Artificial flavors, doesn't taste like Cappucc...
1949730    The seal was broken when it arrived. It was su...
326633     At first my husband ordered this garri and we ...
967783     When the cholula arrived one of the two bottle...
                                 ...                        
350221     This sauce taste like bad sauce. It has a chem...
2219605    This seems to me to be vastly over-rated. It's...
841664     I have tried these products. They have a Beer ...
564356     This is the first time we've been able to use ...
1721726    I received these and they were all chunky and ...
Name: review_body, Length: 10000, dtype: object

In [ ]:
# Import the wordcloud library
from wordcloud import WordCloud
# Join the different processed titles together.
long_string = ','.join(list(data['review_body'].values))
# Create a WordCloud object
wordcloud = WordCloud(background_color="white", max_words=5000, contour_width=3, contour_color='steelblue')
# Generate a word cloud
wordcloud.generate(long_string)
# Visualize the word cloud
wordcloud.to_image()

In [31]:
stop_words = stopwords.words('english')
stop_words.extend(['br'])

def sent_to_words(sentences):
    for sentence in sentences:
        yield(nltk.word_tokenize(str(sentence)))
        
def remove_stopwords(texts):
    return [[(te,ta) for (te,ta) in doc if (te.replace("NEG","") not in stop_words) and te not in "[,\.!?]<>$£/*()%^&-_=+|#~;:..."] for doc in texts]

data_filtered = data
data_words = list(sent_to_words(data_filtered))
# remove stop words
#data_words = remove_stopwords(data_words)
pprint.pprint(data_words[:5])
#np.array(data_words[0], dtype=object).shape

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel\ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
<>:9: DeprecationWarning: invalid escape sequence \.
<>:9: DeprecationWarning: invalid escape sequence \.
<ipython-input-31-9d4e406e97d0>:9: DeprecationWarning: invalid escape sequence \.
  return [[(te,ta) for (te,ta) in doc if (te.replace("NEG","") not in stop_words) and te not in "[,\.!?]<>$£/*()%^&-_=+|#~;:..."] for doc in texts]


[['The',
  'centers',
  'of',
  'these',
  'products',
  'were',
  'to',
  'be',
  'filled',
  'with',
  'Kirsch',
  'brandy',
  'syrup',
  '.',
  'Alas',
  ',',
  'there',
  'was',
  'no',
  'brandy',
  'and',
  'in',
  'fact',
  'no',
  'center',
  'at',
  'all',
  'as',
  'they',
  'had',
  'caved',
  'in',
  '.',
  'The',
  'chocolate',
  'tasted',
  'old',
  'and',
  'I',
  'gave',
  'it',
  'to',
  'various',
  'family',
  'and',
  'friends',
  'and',
  'none',
  'liked',
  'this',
  'brand',
  '.',
  'I',
  'buy',
  'a',
  'lot',
  'of',
  'specialty',
  'chocolate',
  'and',
  'was',
  'VERY',
  'disappointed',
  'with',
  'this',
  'purchase',
  '.',
  'Will',
  'not',
  'be',
  'buying',
  'anymore',
  'Camille',
  'Bloch',
  '.'],
 ['Artificial',
  'flavors',
  ',',
  'does',
  "n't",
  'taste',
  'like',
  'Cappuccino',
  'at',
  'all',
  '.',
  'Threw',
  'the',
  'product',
  'away',
  '-',
  'money',
  'down',
  'the',
  'drain',
  '.',
  'This',
  'product',
  'is',
  '

In [32]:
data_words = [[word.lower() for word in data_point] for data_point in data_words]
data_words

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel\ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


[['the',
  'centers',
  'of',
  'these',
  'products',
  'were',
  'to',
  'be',
  'filled',
  'with',
  'kirsch',
  'brandy',
  'syrup',
  '.',
  'alas',
  ',',
  'there',
  'was',
  'no',
  'brandy',
  'and',
  'in',
  'fact',
  'no',
  'center',
  'at',
  'all',
  'as',
  'they',
  'had',
  'caved',
  'in',
  '.',
  'the',
  'chocolate',
  'tasted',
  'old',
  'and',
  'i',
  'gave',
  'it',
  'to',
  'various',
  'family',
  'and',
  'friends',
  'and',
  'none',
  'liked',
  'this',
  'brand',
  '.',
  'i',
  'buy',
  'a',
  'lot',
  'of',
  'specialty',
  'chocolate',
  'and',
  'was',
  'very',
  'disappointed',
  'with',
  'this',
  'purchase',
  '.',
  'will',
  'not',
  'be',
  'buying',
  'anymore',
  'camille',
  'bloch',
  '.'],
 ['artificial',
  'flavors',
  ',',
  'does',
  "n't",
  'taste',
  'like',
  'cappuccino',
  'at',
  'all',
  '.',
  'threw',
  'the',
  'product',
  'away',
  '-',
  'money',
  'down',
  'the',
  'drain',
  '.',
  'this',
  'product',
  'is',
  '

import nltk.sentiment.util
tokens = list(map(nltk.word_tokenize, data))
negated_tokens = list(map(nltk.sentiment.util.mark_negation, tokens))
data = negated_tokens

In [33]:
#print(data_words)
def tag(texts):
    #tokens = list(map(nltk.word_tokenize, texts))
    tagged = [nltk.pos_tag(text, tagset='universal') for text in texts]
    negated_tokens = list(map(nltk.sentiment.util.mark_negation, texts))
    negated_tagged = [[(negated_tokens[i][j], tagged[i][j][1]) for j in range(len(texts[i]))] for i in range(len(texts))]
    return negated_tagged
negated_tagged = tag(data_words)
negated_tagged

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel\ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


[[('the', 'DET'),
  ('centers', 'NOUN'),
  ('of', 'ADP'),
  ('these', 'DET'),
  ('products', 'NOUN'),
  ('were', 'VERB'),
  ('to', 'PRT'),
  ('be', 'VERB'),
  ('filled', 'VERB'),
  ('with', 'ADP'),
  ('kirsch', 'NOUN'),
  ('brandy', 'NOUN'),
  ('syrup', 'NOUN'),
  ('.', '.'),
  ('alas', 'NOUN'),
  (',', '.'),
  ('there', 'DET'),
  ('was', 'VERB'),
  ('no', 'DET'),
  ('brandy_NEG', 'NOUN'),
  ('and_NEG', 'CONJ'),
  ('in_NEG', 'ADP'),
  ('fact_NEG', 'NOUN'),
  ('no_NEG', 'DET'),
  ('center_NEG', 'NOUN'),
  ('at_NEG', 'ADP'),
  ('all_NEG', 'DET'),
  ('as_NEG', 'ADP'),
  ('they_NEG', 'PRON'),
  ('had_NEG', 'VERB'),
  ('caved_NEG', 'VERB'),
  ('in_NEG', 'ADP'),
  ('.', '.'),
  ('the', 'DET'),
  ('chocolate', 'NOUN'),
  ('tasted', 'VERB'),
  ('old', 'ADJ'),
  ('and', 'CONJ'),
  ('i', 'ADJ'),
  ('gave', 'VERB'),
  ('it', 'PRON'),
  ('to', 'PRT'),
  ('various', 'ADJ'),
  ('family', 'NOUN'),
  ('and', 'CONJ'),
  ('friends', 'NOUN'),
  ('and', 'CONJ'),
  ('none', 'NOUN'),
  ('liked_NEG', 'VERB')

In [34]:
data_words = remove_stopwords(negated_tagged)
data_words

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel\ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


[[('centers', 'NOUN'),
  ('products', 'NOUN'),
  ('filled', 'VERB'),
  ('kirsch', 'NOUN'),
  ('brandy', 'NOUN'),
  ('syrup', 'NOUN'),
  ('alas', 'NOUN'),
  ('brandy_NEG', 'NOUN'),
  ('and_NEG', 'CONJ'),
  ('in_NEG', 'ADP'),
  ('fact_NEG', 'NOUN'),
  ('no_NEG', 'DET'),
  ('center_NEG', 'NOUN'),
  ('at_NEG', 'ADP'),
  ('all_NEG', 'DET'),
  ('as_NEG', 'ADP'),
  ('they_NEG', 'PRON'),
  ('had_NEG', 'VERB'),
  ('caved_NEG', 'VERB'),
  ('in_NEG', 'ADP'),
  ('chocolate', 'NOUN'),
  ('tasted', 'VERB'),
  ('old', 'ADJ'),
  ('gave', 'VERB'),
  ('various', 'ADJ'),
  ('family', 'NOUN'),
  ('friends', 'NOUN'),
  ('none', 'NOUN'),
  ('liked_NEG', 'VERB'),
  ('this_NEG', 'DET'),
  ('brand_NEG', 'NOUN'),
  ('buy', 'VERB'),
  ('lot', 'NOUN'),
  ('specialty', 'NOUN'),
  ('chocolate', 'NOUN'),
  ('disappointed', 'ADJ'),
  ('purchase', 'NOUN'),
  ('be_NEG', 'VERB'),
  ('buying_NEG', 'VERB'),
  ('anymore_NEG', 'ADV'),
  ('camille_NEG', 'ADJ'),
  ('bloch_NEG', 'NOUN')],
 [('artificial', 'ADJ'),
  ('flavors',

In [35]:
def get_adjectives(tagged):
    review_a = [word for (word, tag) in tagged if tag == 'ADJ']
    return review_a

data_words = list(map(lambda x: get_adjectives(x), data_words))

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel\ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [36]:
# Create Dictionary
id2word = corpora.Dictionary(data_words)
# Create Corpus
texts = data_words
# Term Document Frequency
corpus = [id2word.doc2bow(text) for text in texts]
# View
pprint.pprint(corpus[:5])

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel\ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


[[(0, 1), (1, 1), (2, 1), (3, 1)],
 [(4, 1), (5, 1), (6, 1)],
 [(7, 1)],
 [(1, 1), (8, 1), (9, 1)],
 [(1, 1)]]


In [37]:
# number of topics
num_topics = 3
# Build LDA model
lda_model = gensim.models.LdaMulticore(corpus=corpus,
                                       id2word=id2word,
                                       num_topics=num_topics,
                                       minimum_probability=0.1,
                                       workers=3,
                                       passes=2)
# Print the Keyword in the 10 topics
pprint.pprint(lda_model.print_topics())
doc_lda = lda_model[corpus]

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel\ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


[(0,
  '0.026*"good_NEG" + 0.015*"i_NEG" + 0.015*"horrible" + 0.011*"many" + '
  '0.009*"bad" + 0.009*"big" + 0.008*"hard" + 0.008*"great" + '
  '0.008*"disappointed" + 0.008*"nasty"'),
 (1,
  '0.022*"disappointed" + 0.014*"good" + 0.014*"awful" + 0.014*"old" + '
  '0.014*"great" + 0.012*"bad" + 0.010*"terrible" + 0.009*"i_NEG" + '
  '0.009*"gross" + 0.009*"less"'),
 (2,
  '0.027*"good" + 0.017*"first" + 0.016*"bad" + 0.013*"small" + 0.012*"i_NEG" '
  '+ 0.011*"different" + 0.010*"new" + 0.010*"little" + 0.009*"much" + '
  '0.009*"best"')]


In [38]:
pprint.pprint(lda_model.print_topics(num_topics=100))

[(0,
  '0.026*"good_NEG" + 0.015*"i_NEG" + 0.015*"horrible" + 0.011*"many" + '
  '0.009*"bad" + 0.009*"big" + 0.008*"hard" + 0.008*"great" + '
  '0.008*"disappointed" + 0.008*"nasty"'),
 (1,
  '0.022*"disappointed" + 0.014*"good" + 0.014*"awful" + 0.014*"old" + '
  '0.014*"great" + 0.012*"bad" + 0.010*"terrible" + 0.009*"i_NEG" + '
  '0.009*"gross" + 0.009*"less"'),
 (2,
  '0.027*"good" + 0.017*"first" + 0.016*"bad" + 0.013*"small" + 0.012*"i_NEG" '
  '+ 0.011*"different" + 0.010*"new" + 0.010*"little" + 0.009*"much" + '
  '0.009*"best"')]


C:\ProgramData\Anaconda3\lib\site-packages\ipykernel\ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [40]:
from itertools import chain
lda_corpus = lda_model[corpus]

# Find the threshold, let's set the threshold to be 1/#clusters,
# To prove that the threshold is sane, we average the sum of all probabilities:
scores = list(chain(*[[score for topic_id,score in topic] for topic in [doc for doc in lda_corpus]]))
threshold = sum(scores)/len(scores)


C:\ProgramData\Anaconda3\lib\site-packages\ipykernel\ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [41]:
import pickle 
import pyLDAvis
import pyLDAvis.gensim_models
data_vis = pyLDAvis.gensim_models.prepare(lda_model, corpus, id2word)

pyLDAvis.display(data_vis)

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel\ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [42]:
print(threshold)

0.4617973990956625


C:\ProgramData\Anaconda3\lib\site-packages\ipykernel\ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [43]:
cluster1 = [j for i,j in zip(lda_corpus[:100],texts[:100]) if i[0][1] > threshold]
print(1)
cluster2 = [j for i,j in zip(lda_corpus[:100],texts[:100]) if i[1][1] > threshold]
print(2)
cluster3 = [j for i,j in zip(lda_corpus[:100],texts[:100]) if i[2][1] > threshold]
print(3)


1


C:\ProgramData\Anaconda3\lib\site-packages\ipykernel\ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


IndexError: list index out of range

In [ ]:
print(cluster1[:100], "\n \n")
print(cluster2[:100], "\n \n")
print(cluster3[:100], "\n")